# Investment and Trading Capstone Project

## Build a Stock Price Indicator

### project overview

Investment firms, hedge funds and even individuals have been using financial models to better understand market behavior and make profitable investments and trades. A wealth of information is available in the form of historical stock prices and company performance data, suitable for machine learning algorithms to process. 

This project uses this historical stock prices from finnhub.io to make predictions on the development of these stocks. The result of this process will implememnted in a website giving the user the possibility to choose a certain timeframe or stock to analyze.

### problem statement

The problem to be tackled in this project is to predict future adjsuted stock closing prices for certain stocks. To do so we will make use of several regression and deep learning models to achieve a maximum of accuracy for our predictions. 
The user interaction of this project will be implemented in a website/dashboard. There it will be possible to choose the stock of interest and a certain timeframe to predict data for the fututre.

## Exploratory Data Analysis

In this part we will have a closer look at the underlying data to decide how exactly we will deal with it in order to achieve the above mentioned results. Let's read in some libraries and the data first.

In [3]:
import warnings
import pandas as pd
import numpy as np
import requests
from datetime import datetime
from functools import reduce
import plotly.graph_objects as go
from statsmodels.tsa.stattools import adfuller,acf, pacf
from statsmodels.tools.sm_exceptions import ConvergenceWarning
from statsmodels.tsa.seasonal import seasonal_decompose
from statsmodels.tsa.arima_model import ARIMA
# import matplotlib.pyplot as plt

warnings.simplefilter('ignore', ConvergenceWarning)

### data

We obtain our data from an API at www.finnhub.io. We're especially interested in the candlestick data for stocks going back 25 years for US stocks. As an example in this notebook we choose to work the the Google stock (GOOG).

In [4]:
def convert_timestamp_to_unix(timestamp):
    """Converts a pandas timestamp to a unix integer."""
    return (timestamp - pd.Timestamp("1970-01-01")) // pd.Timedelta('1s')

def convert_unix_to_timestamp(unix):
    """Converts a unix integer into a pandas datetime object."""
    return pd.to_datetime(unix, unit='s')

In [85]:
def get_ohlc_data(symbols, timedelta='5y'):
    """
    Queries list of stock symbols for their OHLC data.
    Arguments:
    symbols - list of strings containing the stock symbol of the desired stock
    Returns:
    ohlc_data - dict of dataframes containing ohlc data for each symbol over certain timeframe
    """
    ohlc_data = dict()
    # get start & endtime for ohlc data
    end_time = datetime.now()
    start_time = end_time - pd.Timedelta(timedelta)
    # convert times in unix integers for API request
    to_time = convert_timestamp_to_unix(end_time)
    from_time = convert_timestamp_to_unix(start_time)

    # get OHLC data for each symbol
    for symbol in symbols:
        r = requests.get(
            'https://finnhub.io/api/v1/stock/candle?symbol={}&resolution=D&from={}&to={}&adjusted=true'.format(
            symbol, from_time, to_time))

        data = pd.DataFrame(
            index= [convert_unix_to_timestamp(x).to_period('D') for x in r.json()['t']],
            data = {'open': r.json()['o'],
                    'high': r.json()['h'],
                    'low': r.json()['l'],
                    'adj_close': r.json()['c'],
                    'volume': r.json()['v']})
        ohlc_data.update({symbol: data})
    
    return ohlc_data

In [86]:
symbols = ['GOOG', 'AAPL']
ohlc_data = get_ohlc_data(symbols)

In [7]:
ohlc_data['GOOG'].info()

<class 'pandas.core.frame.DataFrame'>
Index: 1259 entries, 2015-08-21 to 2020-08-20
Data columns (total 5 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   open       1259 non-null   float64
 1   high       1259 non-null   float64
 2   low        1259 non-null   float64
 3   adj_close  1259 non-null   float64
 4   volume     1259 non-null   int64  
dtypes: float64(4), int64(1)
memory usage: 59.0+ KB


In [8]:
ohlc_data['AAPL'].info()

<class 'pandas.core.frame.DataFrame'>
Index: 1259 entries, 2015-08-21 to 2020-08-20
Data columns (total 5 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   open       1259 non-null   float64
 1   high       1259 non-null   float64
 2   low        1259 non-null   float64
 3   adj_close  1259 non-null   float64
 4   volume     1259 non-null   int64  
dtypes: float64(4), int64(1)
memory usage: 59.0+ KB


We can see that for both datapoints we got back a complete dataset without any null values. There is no further cleaning required.

In [9]:
def plot_ohlc(symbols):
    """
    Plots the ohlc data for a given symbol and timeframe.
    Arguments:
    symbols - list of strings representing the name of a stock symbol that is contained in the ohlc dictionary.
    Returns:
    None
    """
    for symbol in symbols:
        
        df = ohlc_data[symbol]

        fig = go.Figure(data=[
            go.Candlestick(
                name=symbol,
                x=df.index,
                open=df.open,
                high=df.high,
                low=df.low,
                close=df.adj_close)])

        fig.update_layout(
            xaxis_rangeslider_visible=False,
            title='OHLC Stock Chart for: {}'.format(symbol))
        fig.show()

In [10]:
plot_ohlc(symbols)

Above we mentioned that there are no missing values in our datasets. However, zooming in we can observe gaps in both of the graphs above. This is due to the fact that the stock markets are closed on weekends and certain holidays. This shouldn't be a problem for our prediction as we want to prodict for predefined steps in the future like 7 or 30 days. The exact day then doesn't really matter.

## Algorithm Evaluation

In this chapter we will have a look on different models to predict stock prices and evaluate their performance to decide which algorithm to implement in the final stock price predictor.

### ARIMA

### TODO: Explain model and prep steps

Most of the models dealing with TimeSeries data work on the assumption that the data is stationary. Stationary means that it's statistical properties such as mean or standard deviation remain constant over time. We can assume the series to be stationary if it has constant statistical properties over time., i.e. the following:
- constant mean
- constant variance
- an autocovariance that doesn't depend on time

In the above graphs we could clearly see an overall increasing trend. We would not expect any seasonal patterns in this data but will also check for this later. To confirm our visual inspection we check for stationarity by using:
- **Plots of the rolling statistics**: We can plot the moving average and moving variance of the adjsuted closing price and see if it changes over time. Here we will use a timeframe of 7 days to catch possible weekly changes.
- **Dickey-Fuller test**: This is a statistical test to check stationarity. The *Null Hypothesis* is that the TimeSeries is not stationary. The results of this test are a *Test Statistic* and some *Critical Values* for different confidence levels. If the Test Statistic is smaller than the Critical Value we can reject the Null Hypothesis and say the series is stationary.

In [11]:
def check_stationarity(timeseries, interval=7):
    """
    Calculates rolling average and std. deviation for a series of adjusted closing prices.
    The function plots the results and prints the results of the Dickey-Fuller test.
    
    Arguments:
    symbol - string containing the stock symbol of the desired stock
    interval - timeframe to calculate rolling statistics
    Returns:
    df - dataframe with added rolling statistics
    """
    
    # add rolling statistics to dataframe  
    roll_avg = timeseries.rolling(interval).mean()
    roll_std = timeseries.rolling(interval).std()
    
    # plot adjusted closing price vs. rolling statistics
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=df.index, y= timeseries, name='Original'))
    fig.add_trace(go.Scatter(x=df.index, y= roll_avg, name='Rolling Average'))
    fig.add_trace(go.Scatter(x=df.index, y= roll_std, name='Rolling Std Deviation'))
    fig.update_layout(title='Rolling Mean & Standard Deviation')
    fig.show()
    
    # Dickey-Fuller test:
    result = adfuller(timeseries)
    print('ADF Statistic: {}'.format(result[0]))
    print('p-value: {}'.format(result[1]))
    print('Critical Values:')
    for key, value in result[4].items():
        print('\t{}: {}'.format(key, value))

From the graph we can tell that our rolling statistics change over time meaning they are not stationary. 
The results from the Dickey-Fuller test confirm our observation. The ADF statistic is way higher than any of our Critical Values here. It's safe to say our series is not stationary and there's some work to do to make it stationary.

In [12]:
df = ohlc_data['GOOG']
timeseries = np.log(df.adj_close)

In [101]:
moving_avg = timeseries.rolling(30).mean()

fig = go.Figure()
fig.add_trace(go.Scatter(x=df.index, y=timeseries,
                    name='Log(adjusted closing price)'))
fig.add_trace(go.Scatter(x=df.index, y=moving_avg,
                    name='Moving Avg'))

ts_log_moving_avg_diff = timeseries - moving_avg
ts_log_moving_avg_diff.dropna(inplace=True)

In [102]:
check_stationarity(ts_log_moving_avg_diff)

ADF Statistic: -7.152492933258068
p-value: 3.11495350631529e-10
Critical Values:
	1%: -3.435761408287299
	5%: -2.863929614852828
	10%: -2.568042270495956


In [103]:
exp_weighted_avg = timeseries.ewm(halflife=30).mean()

fig = go.Figure()
fig.add_trace(go.Scatter(x=df.index, y=timeseries,
                    name='Log(adjusted closing price)'))
fig.add_trace(go.Scatter(x=df.index, y=exp_weighted_avg,
                    name='Exp Moving Avg'))

ts_log_exp_avg_diff = timeseries - exp_weighted_avg
ts_log_exp_avg_diff.dropna(inplace=True)

In [104]:
check_stationarity(ts_log_exp_avg_diff)

ADF Statistic: -5.433676338300417
p-value: 2.8770605657247273e-06
Critical Values:
	1%: -3.435634587707382
	5%: -2.8638736617392837
	10%: -2.568012472034339


In [91]:
def decompose_timeseries(timeseries, period=10):
    """
    Decompose timeseries in trend, seasonal and residual part.
    Plots graph for each partition of timeseries.
    
    Arguments:
    timeseries - timeseries to decompose
    period - timeframe to consider for decompopsition
    Returns:
    trend - trend timeseries w/o NaN values
    seasonal - seasonal series w/o NaN values
    residual - residual timeseries w/o NaN values
    """

    decomposition = seasonal_decompose(x=timeseries, period=period)

    trend = decomposition.trend.dropna()
#     trend.index = pd.DatetimeIndex(trend.index).to_period('D')
    seasonal = decomposition.seasonal.dropna()
#     seasonal.index = pd.DatetimeIndex(seasonal.index).to_period('D')
    residual = decomposition.resid.dropna()
#     residual.index = pd.DatetimeIndex(residual.index).to_period('D')

    fig = go.Figure()
    fig.add_trace(go.Scatter(x=df.index, y=timeseries, name='Original'))
    fig.add_trace(go.Scatter(x=df.index, y=trend, name='Trend'))
    fig.add_trace(go.Scatter(x=df.index, y=seasonal, name='Seasonality'))
    fig.add_trace(go.Scatter(x=df.index, y=residual, name='Residuals'))
    fig.show()
    
    return trend, seasonal, residual

In [105]:
trend, seasonal, residual = decompose_timeseries(timeseries, 30)

In [19]:
check_stationarity(residual)

ADF Statistic: -11.890671150006984
p-value: 5.878990847246854e-22
Critical Values:
	1%: -3.435690695421723
	5%: -2.863898416697677
	10%: -2.5680256555204184


### ARIMA model

#### Auto correlation function (ACF):
This metric expresses the correlation between the observations at the current point in time and the observations at all previous points in time. We use ACF to determine the **number of optimal Moving Average (MA) terms**. 

#### Partial  Auto correlation function (PACF):
PACG expresses the correlation between observations made at two points in time while accounting for any influence from other data points. We sue PACF to determine the **optimal number of Autoregressive terms** in our model. 

In [20]:
def check_auto_correlation(timeseries, n_lags):
    """
    Calculates and plots Autocorrelation function (ACF) & Partial Autocorrelation function (PACF).
    Plots the results and the related confidence interval.
    """
        
    lag_acf, conf_array = acf(timeseries, nlags=n_lags, fft=True, alpha=0.05)
    upper = conf_array[:, 1] - lag_acf
    lower = conf_array[:, 0] - lag_acf
    lag_pacf = pacf(timeseries, nlags=n_lags, method='ols')

    # Plot ACF & PACF
    x = list(range(1,n_lags))
    x_rev = x[::-1]
    lower = lower[::-1]

    fig = go.Figure()
    fig.add_trace(go.Scatter(x=x, y=lag_acf, name='ACF'))
    fig.add_trace(go.Scatter(x=x, y=lag_pacf, name='PACF'))
    fig.add_trace(go.Scatter(x=x, y=upper, name='upper conf-int',
                            mode='lines', fill='tozeroy'))
    fig.add_trace(go.Scatter(x=x, y=lower[::-1], name='lower conf-int',
                            mode='lines', fill='tozeroy'))
    fig.show()

In [88]:
check_auto_correlation(residual, 10)

### Choosing the inputs for the ARIMA model

With the above chart we look for the values p, d & q as inputs for our model which are described as followed: 
p: number of autoregressive terms (AR order)
d: number of nonseasonal differences (differencing order)
q: number of moving-average terms (MA order)

Therfore we choose the values as follows:

In [37]:
p, d, q = 2, 0, 2

In [53]:
def plot_fitting(residual, model_results):
    """Plots the residual values vs the fitted values for comparison."""
    
    if model_results.k_ar != 0 & model_results.k_ma == 0:
        model_type = 'AR Model'
    elif model_results.k_ar == 0 & model_results.k_ma != 0:
        model_type = 'MA Model'
    else: 
        model_type = 'ARIMA model'
    sse = sum((model_results.fittedvalues-residual)**2)
        
    x = residual.index.to_timestamp()
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=x, y=residual, name='Residuals'))
    fig.add_trace(go.Scatter(x=x, y=model_results.fittedvalues, name='Fitted Values'))
    fig.update_layout(title='{} \t-\t SSE: {:.4f}'.format(model_type, sse))
    fig.show()

In [55]:
# AR model
model = ARIMA(residual, order=(p, d, 0))  
results_AR = model.fit(disp=-1)  
plot_fitting(residual, results_AR)

# MA model
model = ARIMA(residual, order=(0, d, q))  
results_MA = model.fit(disp=-1)  
plot_fitting(residual, results_MA)

# combined ARIMA model
model = ARIMA(residual, order=(p, d, q))  
results_ARIMA = model.fit(disp=-1)  
plot_fitting(residual, results_ARIMA)

In [82]:
predictions_ARIMA_diff = pd.Series(results_ARIMA.fittedvalues, copy=True)
predictions_ARIMA_diff_cumsum = predictions_ARIMA_diff.cumsum()

common_idx = reduce(np.intersect1d, (residual.index, trend.index, seasonal.index, predictions_ARIMA_diff_cumsum.index))
agg_values = reduce(np.add, (residual[common_idx], predictions_ARIMA_diff_cumsum[common_idx], trend[common_idx], seasonal[common_idx]))

predictions_ARIMA  = np.exp(agg_values)
rmse = np.sqrt(sum((predictions_ARIMA-np.exp(timeseries[common_idx]))**2)/len(timeseries[common_idx]))

fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=np.exp(timeseries), name='Original'))
fig.add_trace(go.Scatter(x=x, y=predictions_ARIMA, name='Predicition'))
fig.update_layout(title='RMSE: {:.4f}'.format(rmse))

From the chart above we can tell that our predicted values are quite far away from the original data. This is confirmed by an RMSE of ~180. A prediction that can be that far from the actual value is not acceptable for stock prices.

## LSTM